# PageRank
The PageRank algorithm produces a probability distribution representing the likelihood that a person randomly traversing a graph will arrive at any particular vertex. PageRank was added in MADlib 1.11.

We also implement personalized PageRank, in which a notion of importance provides personalization to a query. This was added in 1.14

In [1]:
%load_ext sql

In [2]:
# Greenplum Database 5.x on GCP (PM demo machine) - via tunnel
%sql postgresql://gpadmin@localhost:8000/madlib
        
# PostgreSQL local
#%sql postgresql://fmcquillan@localhost:5432/madlib

In [3]:
%sql select madlib.version();
#%sql select version();

1 rows affected.


[(u'MADlib version: 1.18.0-dev, git revision: rel/v1.17.0-100-g4987e8f, cmake configuration time: Wed Mar 24 23:51:47 UTC 2021, build type: release, build system: Linux-3.10.0-1160.21.1.el7.x86_64, C compiler: gcc 4.8.5, C++ compiler: g++ 4.8.5',)]

# 1.  Create vertex and edge tables

In [4]:
%%sql 
DROP TABLE IF EXISTS vertex, edge;

CREATE TABLE vertex(
        id INTEGER
        );

CREATE TABLE edge(
        src INTEGER,
        dest INTEGER,
        user_id INTEGER
        );

INSERT INTO vertex VALUES
(0),
(1),
(2),
(3),
(4),
(5),
(6);

INSERT INTO edge VALUES
(0, 1, 1),
(0, 2, 1),
(0, 4, 1),
(1, 2, 1),
(1, 3, 1),
(2, 3, 1),
(2, 5, 1),
(2, 6, 1),
(3, 0, 1),
(4, 0, 1),
(5, 6, 1),
(6, 3, 1),
(0, 1, 2),
(0, 2, 2),
(0, 4, 2),
(1, 2, 2),
(1, 3, 2),
(2, 3, 2),
(3, 0, 2),
(4, 0, 2),
(5, 6, 2),
(6, 3, 2);

SELECT * from edge ORDER BY src;

Done.
Done.
Done.
7 rows affected.
22 rows affected.
22 rows affected.


[(0, 1, 1),
 (0, 2, 2),
 (0, 2, 1),
 (0, 4, 2),
 (0, 4, 1),
 (0, 1, 2),
 (1, 3, 1),
 (1, 3, 2),
 (1, 2, 2),
 (1, 2, 1),
 (2, 5, 1),
 (2, 3, 1),
 (2, 3, 2),
 (2, 6, 1),
 (3, 0, 2),
 (3, 0, 1),
 (4, 0, 1),
 (4, 0, 2),
 (5, 6, 2),
 (5, 6, 1),
 (6, 3, 1),
 (6, 3, 2)]

# 2.  Calculate PageRank

In [5]:
%%sql
DROP TABLE IF EXISTS pagerank_out, pagerank_out_summary;

SELECT madlib.pagerank(
                         'vertex',             -- Vertex table
                         'id',                 -- Vertix id column
                         'edge',               -- Edge table
                         'src=src, dest=dest', -- Comma delimted string of edge arguments
                         'pagerank_out');      -- Output table of PageRank

SELECT * FROM pagerank_out ORDER BY pagerank DESC;

Done.
1 rows affected.
7 rows affected.


[(0, 0.287518161212111),
 (3, 0.210171199451415),
 (2, 0.146637377532288),
 (4, 0.102910437211324),
 (1, 0.102910437211324),
 (6, 0.0972746644343418),
 (5, 0.0525777229481976)]

Look at the summary table:

In [7]:
%%sql
SELECT * FROM pagerank_out_summary;

1 rows affected.


[(12,)]

Now run PageRank with a damping factor of 0.5 which results in different final values:

# 3.  Calculate PageRank with optional params

In [6]:
%%sql
DROP TABLE IF EXISTS pagerank_out, pagerank_out_summary;
SELECT madlib.pagerank(
                         'vertex',             -- Vertex table
                         'id',                 -- Vertix id column
                         'edge',               -- Edge table
                         'src=src, dest=dest', -- Comma delimted string of edge arguments
                         'pagerank_out',       -- Output table of PageRank
                         0.5);                 -- Damping factor
SELECT * FROM pagerank_out ORDER BY pagerank DESC;

Done.
1 rows affected.
7 rows affected.


[(0, 0.225477430555642),
 (3, 0.199105076058278),
 (2, 0.136259748401728),
 (6, 0.132687846188875),
 (4, 0.109006420855422),
 (1, 0.109006420855422),
 (5, 0.0884570570850217)]

# 4. Grouping
Now compute the PageRank distribution separately for each user using the grouping feature:

In [7]:
%%sql
DROP TABLE IF EXISTS pagerank_out, pagerank_out_summary;

SELECT madlib.pagerank(
                         'vertex',             -- Vertex table
                         'id',                 -- Vertix id column
                         'edge',               -- Edge table
                         'src=src, dest=dest', -- Comma delimted string of edge arguments
                         'pagerank_out',       -- Output table of PageRank
                         NULL,                 -- Default damping factor (0.85)
                         NULL,                 -- Default max iters (100)
                         0.00000001,           -- Threshold
                         'user_id');           -- Grouping column name

SELECT * FROM pagerank_out ORDER BY user_id, pagerank DESC;

Done.
1 rows affected.
14 rows affected.


[(1, 0L, 0.278254883885528),
 (1, 3L, 0.201881146670752),
 (1, 2L, 0.142881123460599),
 (1, 6L, 0.114536378321472),
 (1, 4L, 0.10026745615438),
 (1, 1L, 0.10026745615438),
 (1, 5L, 0.0619115553528898),
 (2, 0L, 0.318546250041731),
 (2, 3L, 0.237866867733431),
 (2, 2L, 0.159148764893974),
 (2, 1L, 0.111683344379718),
 (2, 4L, 0.111683344379718),
 (2, 6L, 0.0396428571428571),
 (2, 5L, 0.0214285714285714)]

In [11]:
%%sql
SELECT * FROM pagerank_out_summary ORDER BY user_id;

2 rows affected.


[(1, 27), (2, 31)]

# 5. Personalized PageRank
Here we specify {2,4} as the personalization vertices. This parameter could be specified as ARRAY[2,4] as well:

In [12]:
%%sql
DROP TABLE IF EXISTS pagerank_out, pagerank_out_summary;
SELECT madlib.pagerank(
                       'vertex',             -- Vertex table
                       'id',                 -- Vertix id column
                       'edge',               -- Edge table
                       'src=src, dest=dest', -- Comma delimted string of edge arguments
                       'pagerank_out',       -- Output table of PageRank
                        NULL,                -- Default damping factor (0.85)
                        NULL,                -- Default max iters (100)
                        NULL,                -- Default Threshold
                        NULL,                -- No Grouping
                       '{2,4}');             -- Personalization vertices
SELECT * FROM pagerank_out ORDER BY pagerank DESC;

Done.
1 rows affected.
7 rows affected.


[(0, 0.282616480980651),
 (2, 0.18906971049691),
 (3, 0.177501646133459),
 (4, 0.155055607949638),
 (1, 0.0800556079496381),
 (6, 0.0743076577867786),
 (5, 0.0401701653567887)]

In [14]:
%%sql
SELECT * FROM pagerank_out_summary;

1 rows affected.


[(37,)]